# Check change in mean slope
- Check the effect of changes in prestorm and poststorm mean slope.
- If there is a large berm, the prestorm mean slope (between dune toe and MHW) could be too small, and underpredict wave runup and TWL.


## Setup notebook

In [ ]:
# Enable autoreloading of our modules. 
# Most of the code will be located in the /src/ folder, 
# and then called from the notebook.
%matplotlib inline
%reload_ext autoreload
%autoreload

In [ ]:
from IPython.core.debugger import set_trace

import pandas as pd
import numpy as np
import os

import plotly
import plotly.graph_objs as go
import plotly.plotly as py
import plotly.tools as tools
import plotly.figure_factory as ff
import plotly.io as pio

import itertools

import matplotlib
from matplotlib import cm
import colorlover as cl

from ipywidgets import widgets, Output
from IPython.display import display, clear_output, Image, HTML
import matplotlib.pyplot as plt
from sklearn.metrics import confusion_matrix

In [ ]:
# Matplot lib default settings
plt.rcParams["figure.figsize"] = (10,6)
plt.rcParams['axes.grid']=True
plt.rcParams['grid.alpha'] = 0.5
plt.rcParams['grid.color'] = "grey"
plt.rcParams['grid.linestyle'] = "--"
plt.rcParams['axes.grid']=True

# https://stackoverflow.com/a/20709149
matplotlib.rcParams['text.usetex'] = True

matplotlib.rcParams['text.latex.preamble'] = [
       r'\usepackage{siunitx}',   # i need upright \micro symbols, but you need...
       r'\sisetup{detect-all}',   # ...this to force siunitx to actually use your fonts
       r'\usepackage{helvet}',    # set the normal font here
       r'\usepackage{amsmath}',
       r'\usepackage{sansmath}',  # load up the sansmath so that math -> helvet
       r'\sansmath',              # <- tricky! -- gotta actually tell tex to use!
]  

## Import data
Import our data into pandas Dataframes for the analysis. Data files are `.csv` files which are stored in the `./data/interim/` folder.

In [ ]:
def df_from_csv(csv, index_col, data_folder='../data/interim'):
    print('Importing {}'.format(csv))
    return pd.read_csv(os.path.join(data_folder,csv), index_col=index_col)

df_waves = df_from_csv('waves.csv', index_col=[0, 1])
df_tides = df_from_csv('tides.csv', index_col=[0, 1])
df_profiles = df_from_csv('profiles.csv', index_col=[0, 1, 2])
df_sites = df_from_csv('sites.csv', index_col=[0])
df_profile_features_crest_toes = df_from_csv('profile_features_crest_toes.csv', index_col=[0,1])

# Note that the forecasted data sets should be in the same order for impacts and twls
impacts = {
    'forecasted': {
        'foreshore_slope_sto06': df_from_csv('impacts_forecasted_foreshore_slope_sto06.csv', index_col=[0]),
        'mean_slope_sto06': df_from_csv('impacts_forecasted_mean_slope_sto06.csv', index_col=[0]),
        },
    'observed': df_from_csv('impacts_observed.csv', index_col=[0])
    }


twls = {
    'forecasted': {
        'foreshore_slope_sto06': df_from_csv('twl_foreshore_slope_sto06.csv', index_col=[0, 1]),
        'mean_slope_sto06':df_from_csv('twl_mean_slope_sto06.csv', index_col=[0, 1]),
    }
}
print('Done!')

# Plot prestorm vs poststorm mean slopes
Prestorm slopes have already been calculated as part of the TWL forecasting, however we'll need to extract the poststorm mean slopes from our profiles at each site.

In [ ]:
# Prestorm slopes are easy as we have already calculated this as part of the 
df_slopes_prestorm = twls['forecasted']['mean_slope_sto06'].groupby('site_id').head(1).reset_index().set_index(['site_id']).beta.to_frame()

# Get x and z at mhw (z=0.7m) for each site
z_mhw = 0.7
mhw_poststorm = []
for site, df in df_profiles.xs('poststorm', level='profile_type').groupby('site_id'):
    df = df.dropna(subset=['z'])
    df = df.iloc[(df['z']-z_mhw).abs().argsort().head(1)].reset_index()
    df = df.iloc[0]
    mhw_poststorm.append({
        'site_id': df.site_id,
        'x_mhw': df.x,
        'z_mhw': df.z
    })
#     break
df_mhw_poststorm = pd.DataFrame(mhw_poststorm)
df_mhw_poststorm = df_mhw_poststorm.set_index('site_id')

# Get x and z at poststorm dune toe for each site
df_dune_toe_poststorm = df_profile_features_crest_toes.xs('poststorm', level='profile_type')[['dune_toe_x','dune_toe_z']]

# If there is no poststorm dune toe defined, use the dune crest
df_dune_crest_poststorm = df_profile_features_crest_toes.xs('poststorm', level='profile_type')[['dune_crest_x','dune_crest_z']]
df_dune_toe_poststorm.dune_toe_x = df_dune_toe_poststorm.dune_toe_x.fillna(df_dune_crest_poststorm.dune_crest_x)
df_dune_toe_poststorm.dune_toe_z = df_dune_toe_poststorm.dune_toe_z.fillna(df_dune_crest_poststorm.dune_crest_z)


# Join df for mhw and dune toe
df = df_mhw_poststorm.join(df_dune_toe_poststorm)
df['beta'] = -(df['dune_toe_z'] - df['z_mhw']) / (df['dune_toe_x'] -df['x_mhw'])
df_slopes_poststorm = df['beta'].to_frame()

# Count how many nans
print('Number of nans: {}'.format(df_slopes_poststorm.beta.isna().sum()))

# Display dataframe
print('df_slopes_poststorm:')
df_slopes_poststorm

Now, let's join our post storm slopes, prestorm slopes, observed and forecasted impacts into one data frame to make it easier to plot.

In [ ]:
dfs = [df_slopes_poststorm.rename(columns={'beta':'poststorm_beta'}),
    df_slopes_prestorm.rename(columns={'beta':'prestorm_beta'}),
    impacts['observed']['storm_regime'].to_frame().rename(columns={'storm_regime': 'observed_regime'}),
    impacts['forecasted']['mean_slope_sto06']['storm_regime'].to_frame().rename(columns={'storm_regime': 'forecasted_regime'})
      ]

df = pd.concat(dfs, axis='columns')
df

We also should add the change in beach width between prestorm and post storm profiles

In [ ]:
ele = 0.7
data = []
for site_id, df_site in df_profiles.groupby('site_id'):
    
    # Beach width should be measured from dune toe (or crest if doesn't exist) to MHW
    
    dune_toe_x = np.nanmax([
        df_profile_features_crest_toes.loc[(site_id,'prestorm')].dune_crest_x,
        df_profile_features_crest_toes.loc[(site_id,'prestorm')].dune_toe_x
    ])
    
    
    # TODO This probably should take the closest value to ele starting from the seaward end of the profile
    temp = df_site.xs('prestorm',level='profile_type').dropna(subset=['z'])
    prestorm_width = temp.iloc[(temp.z - ele).abs().argsort()[0]].name[1] - dune_toe_x
    
    temp = df_site.xs('poststorm',level='profile_type').dropna(subset=['z'])
    poststorm_width = temp.iloc[(temp.z - ele).abs().argsort()[0]].name[1] - dune_toe_x
    
    width_change = prestorm_width - poststorm_width
    data.append(
    {
        'site_id': site_id,
        'width_change': width_change,
        'prestorm_width': prestorm_width,
        'poststorm_width': poststorm_width
    })
    
    
    
    
df_width_change = pd.DataFrame(data)
df_width_change = df_width_change.set_index(['site_id'])

# Join with the data
df = df.merge(df_width_change, left_on=['site_id'], right_on=['site_id'])


## Plot our data in a confusion matrix
Superseded

In [ ]:
fig = tools.make_subplots(
    rows=2,
    cols=2,
    specs=[[{}, {}], [{}, {}]],
    subplot_titles=('Swash/Swash',  'Swash/Collision', 
                    'Collision/Swash', 'Collision/Collision'),
 shared_xaxes=True, shared_yaxes=True,)


# Loop through combinations of observed/forecasted swash/collision
data = []
for forecasted_regime, observed_regime in itertools.product(['swash','collision'],repeat=2):
    
    # Get data for this combination 
    query = 'forecasted_regime=="{}" & observed_regime=="{}"'.format(forecasted_regime, observed_regime)
    df_data = df.query(query)
    print(query)
                  
    
    # Determine which subplot to plot results in
    if forecasted_regime == 'swash' and observed_regime == 'swash':
        x_col = 1
        y_col = 1
    elif forecasted_regime == 'collision' and observed_regime == 'collision':
        x_col = 2
        y_col = 2
    elif forecasted_regime == 'swash' and observed_regime == 'collision':
        x_col = 2
        y_col = 1
    elif forecasted_regime == 'collision' and observed_regime == 'swash':
        x_col = 1
        y_col = 2
    else:
        print('something went wrong')
        continue

    fig.append_trace(
        go.Scatter(
            x=df_data.prestorm_beta,
            y=df_data.poststorm_beta,
            text = df_data.index.tolist(),
            hoverinfo = 'text',
            mode = 'markers',
            line = dict(
        color = ('rgba(22, 22, 22, 0.2)'),
        width = 0.5,)),
            x_col,
            y_col)

# layout = go.Layout(
#     xaxis=dict(domain=[0, 0.45]),
#     yaxis=dict(
#         domain=[0, 0.45],
#         type='log',
#     ),
#     xaxis2=dict(domain=[0.55, 1]),
#     xaxis4=dict(domain=[0.55, 1], anchor='y4'),
#     yaxis3=dict(
#         domain=[0.55, 1],
#         type='log',
#     ),
#     yaxis4=dict(
#         domain=[0.55, 1],
#         anchor='x4',
#         type='log',
#     ))

fig['layout'].update(showlegend=False, title='Specs with Subplot Title',height=800,)

for ax in ['yaxis','yaxis2']:
#     fig['layout'][ax]['type']='log'
    fig['layout'][ax]['range']= [0,0.2]

for ax in ['xaxis', 'xaxis2']:
    fig['layout'][ax]['range']= [0,0.2]

go.FigureWidget(fig)

Looking at the above plot:
- In general, we can see that the prestorm mean slope is flatter than the poststorm mean slope. This can be explained by the presence of prestorm berms, which increase the prestorm mean slope. During the storm, these berms get eroded and decrease the slope.
- **Collision/Collision**: Where we observe and predict collision, we see steeper prestorm slopes. This is to be expected since larger slopes will generate more runup and higher TWLs.
- **Swash/Collision**: Where we predict collision but observe swash, we can see that the prestorm mean slopes >0.1 generate high TWLs. 



## Plot our data in a confusion matrix


In [ ]:
df[cc_mask].loc[df[cc_mask].poststorm_beta+0.05< df[cc_mask].prestorm_beta]

In [ ]:
f, ([ax1, ax2], [ax3, ax4],) = plt.subplots(
    2,
    2,
    sharey=True,
    sharex=True,
    figsize=(8, 7))


ss_mask = (df.observed_regime=='swash') & (df.forecasted_regime=='swash')
sc_mask = (df.observed_regime=='swash') & (df.forecasted_regime=='collision')
cs_mask = (df.observed_regime=='collision') & (df.forecasted_regime=='swash')
cc_mask = (df.observed_regime=='collision') & (df.forecasted_regime=='collision')

# Define colormap for our observations
cm = plt.cm.get_cmap('plasma')

params = {'edgecolors': '#999999',
          's': 12,
          'linewidth': 0.1, 
          'cmap':cm,
          'vmin':0, 
          'vmax':60
         }

sc=ax1.scatter(df[ss_mask].prestorm_beta, df[ss_mask].poststorm_beta, c=df[ss_mask].width_change,**params)
ax1.set_title('Swash/Swash')
ax1.set_ylabel('Observed swash')

ax2.scatter(df[sc_mask].prestorm_beta, df[sc_mask].poststorm_beta, c=df[sc_mask].width_change,**params)
ax2.set_title('Swash/Collision')

ax3.scatter(df[cs_mask].prestorm_beta, df[cs_mask].poststorm_beta, c=df[cs_mask].width_change,**params)
ax3.set_title('Collision/Swash')
ax3.set_ylabel('Observed collision')
ax3.set_xlabel('Predicted swash')

ax4.scatter(df[cc_mask].prestorm_beta, df[cc_mask].poststorm_beta, c=df[cc_mask].width_change,**params)
ax4.set_title('Collision/Collision')
ax4.set_xlabel('Predicted collision')

for ax in [ax1,ax2,ax3,ax4]:
    ax.plot([0,0.2],[0,0.2], 'k--')
    ax.set_xlim([0,0.2])
    ax.set_ylim([0,0.2])

    
# Create a big ax so we can use common axis labels
# https://stackoverflow.com/a/36542971
f.add_subplot(111, frameon=False)
plt.tick_params(labelcolor='none', top=False, bottom=False, left=False, right=False)
plt.grid(False)
plt.xlabel("Prestorm mean slope (-)", labelpad=25)
plt.ylabel("Poststorm mean slope (-)", labelpad=25)
    
# Layout adjustment
plt.tight_layout()
plt.subplots_adjust(hspace=0.25, bottom=0.1,right=0.9)

# Add colorbar
cbar_ax = f.add_axes([0.95, 0.15, 0.05, 0.7])
cb = f.colorbar(sc, cax=cbar_ax)
cb.set_label(r'$\varDelta$ beach width at MHW (m)')

# Save and show figure
plt.savefig('06-confusion-change-in-slope.png'.format(beach), dpi=600, bbox_inches='tight') 
plt.show()
plt.close()

## Plot for single beach

In [ ]:
beach = 'NARRA'

df_beach = df.loc[df.index.str.contains(beach)]

# Get index
n = [x for x in range(len(df_beach))][::-1]
n_sites = [x for x in df_beach.index][::-1]

f, (ax1,ax2,ax3,ax4) = plt.subplots(1,4, sharey=True,figsize=(10, 8))

ax1.plot(df_beach.prestorm_beta,n,label='Prestorm slope',color='#4d9221')
ax1.plot(df_beach.poststorm_beta,n,label='Poststorm slope',color='#c51b7d')
ax1.set_title('Mean beach slope')
ax1.legend(loc='center', bbox_to_anchor=(0.5, -0.15))

# Replace yticks with site_ids
yticks = ax1.get_yticks().tolist()
yticks = [n_sites[int(y)] if 0 <= y <= len(n_sites) else y for y in yticks ]
ax1.set_yticklabels(yticks)
ax1.set_xlabel(r'Slope (-)')

ax2.plot(df_beach.prestorm_width,n,label='Prestorm width',color='#4d9221')
ax2.plot(df_beach.poststorm_width,n, label='Poststorm width',color='#c51b7d')
# ax2.set_xlim([200,300])
ax2.set_xlabel(r'Beach width (m)')
ax2.set_title('Beach width\nat MHW')
ax2.legend(loc='center', bbox_to_anchor=(0.5, -0.15))

ax3.plot(df_beach.width_change,n,color='#999999')
ax3.set_xlim([0,75])
ax3.set_title('Change in MHW\nbeach width')
ax3.set_xlabel(r'$\varDelta$ Beach width (m)')


ax4.plot(df_beach.poststorm_beta / df_beach.prestorm_beta,n,color='#999999')
ax4.set_title('Ratio between pre and\npost storm mean slopes')

plt.tight_layout()
f.subplots_adjust(top=0.88)
f.suptitle(beach)

# Print to figure
plt.savefig('06-change-in-slope-{}.png'.format(beach), dpi=600, bbox_inches='tight') 
plt.show()
plt.close()

In [ ]:
df_beach